In [1]:
import numpy as np
import geopandas as gp
import pandas as pd
import pysal as ps
import pylab as pl
from shapely.geometry import Point
import seaborn as sns
import shapefile
import mplleaflet
%pylab inline

Populating the interactive namespace from numpy and matplotlib


In [22]:
df = pd.read_csv('source_data/JoinACSFCCPluto.csv')

In [4]:
all_filenames = {}
all_filenames['bk'] = 'shape_by_boro/BK.shp'
all_filenames['bx'] = 'shape_by_boro/BX.shp'
all_filenames['mn'] = 'shape_by_boro/MN.shp'
all_filenames['qn'] = 'shape_by_boro/QN.shp'
all_filenames['si'] = 'shape_by_boro/SI.shp'

master = {}
for k,v in all_filenames.items():
    master[k] = gp.read_file(v)

# set pysal weights

In [5]:
# set geoms
all_geoms = {}

for k,v in all_filenames.items():
    all_geoms[k] = ps.open(v,'r')

In [6]:
# find weight

all_weights = {}

for k,v in all_geoms.items():
    w = ps.buildContiguity(v, criterion='queen')
    w.transorm = 'R'
    all_weights[k] = w


Island id:  [131]


In [7]:
# Save this for column reference
#### Bscore_norm is JoinedD_11
#### FIPS is JoinedDa_1

In [15]:
# glocal Moran

all_sa = {}

for k,v in master.items():
    # normalize these!
    Y = v['JoinedD_11'].values
    w = all_weights[k]
    sl = ps.lag_spatial(w, Y)
    v['w_percent'] = sl
    # global
    mi = ps.Moran(Y,w)
    
    # local Moran
    lisa = ps.Moran_Local(Y, w)
    
    # filter for significance
    S = lisa.p_sim < 0.05

    # put into quadrants
    Q = lisa.q
    
    # add new columns back to original dict
    master[k] = v
    
    # tuple of Global I, Expected I, and significance
    all_sa[k] = mi.I, mi.EI, mi.p_sim,S,Q

In [9]:
for k,v in all_sa.items():
    q1 = 0
    q2 = 0
    q3 = 0
    q4 = 0
    for i in v[4]:
        if i== 1:
            q1 += 1
        elif i==2:
            q2 += 1
        elif i==3:
            q3 += 1
        elif i==4:
            q4 += 1
    print "{}:\nGlobal Moran I of {:.4f} at p={:.4f}".format(k,v[0],v[2])

si:
Global Moran I of 0.1414 at p=0.0030
mn:
Global Moran I of 0.7021 at p=0.0010
bx:
Global Moran I of 0.4874 at p=0.0010
qn:
Global Moran I of 0.8259 at p=0.0010
bk:
Global Moran I of 0.8780 at p=0.0010


QUADRANTS

Q1 = access high (uniformly high access) (q1,pos) high-high

Q2 = access island inequity (low access surrounded by high access) (q2, neg)

Q3 = access low (uniformly low access) (q3,pos) low-low

Q4 = access island available (high access surrounded by low access) (q4, neg)

In [10]:
# plot -- KEEP

# for k,v in master.items():
#     f, ax = pl.subplots(1, figsize=(10,10))
#     sns.regplot(x='JoinedD_11', y='w_percent', data=v)
#     pl.axvline(0, c='k', alpha=0.5)
#     pl.title(k)
# pl.axhline(0, c='k', alpha=0.5);

In [23]:
# reload into a dataframe
new_dfs = {}

for k,v in all_sa.items():
    records = map(lambda x: (master[k].iloc[x]['JoinedDa_1'], v[4][x], master[k].geometry.iloc[x]),
              [i for i,s in enumerate(v[3]) if s])
    new_dfs[k] = gp.GeoDataFrame(records, columns=('FIPS', 'quadrant', 'geometry'))
    new_dfs[k]['FIPS'] = new_dfs[k]['FIPS'].astype(int64)

In [24]:
# merge to old df
final_df = {}

for k,v in new_dfs.items():
    final_df[k] = v.merge(df,how='inner',on='FIPS')
    final_df[k]['boro'] = k

In [25]:
nyc_df_list = []
for k,v in final_df.items():
    nyc_df_list.append(v)

In [26]:
all_nyc = gp.GeoDataFrame(pd.concat(nyc_df_list, ignore_index=True))

In [27]:
all_nyc_map = all_nyc[['FIPS',
 'quadrant',
 'avg_down',
 'avg_up',
 'max_down',
 'max_up',
 'num_providers',
 'num_platforms',
 'top_plat_type',
 'top_plat_ratio',
 'bscore_raw',
 'bscore_norm',
 'BldgArea',
 'ComArea',
 'ResArea',
 'OfficeArea',
 'RetailArea',
 'GarageArea',
 'StrgeArea',
 'FactryArea',
 'NumBldgs',
 'NumFloors',
 'UnitsRes',
 'UnitsTotal',
 'Building Type_Commercial & Office Buildings',
 'Building Type_Industrial & Manufacturing Buildings',
 'Building Type_Mixed Residential & Commercial Buildings',
 'Building Type_Multi-Family Elevator Buildings',
 'Building Type_Multi-Family Walk-Up Buildings',
 'Building Type_One & Two Family Buildings',
 'Building Type_Open Space & Outdoor Recreation',
 'Building Type_Parking Facilities',
 'Building Type_Public Facilities & Institutions',
 'Building Type_Transportation & Utility',
 'Building Type_Vacant Land',
 'Population Density (per sq. mile)',
 'Area (Land)',
 'Area Total:',
 'Area Total: Area (Water)',
 'Total Population:', 'Households:', 'Households: Less than $10_000', 
'Households: $10_000 to $14_999', 'Households: $15_000 to $19_999',
 'Households: $20_000 to $24_999', 'Households: $25_000 to $29_999', 'Households: $30_000 to $34_999', 
 'Households: $35_000 to $39_999', 'Households: $40_000 to $44_999', 'Households: $45_000 to $49_999', 
 'Households: $50_000 to $59_999', 'Households: $60_000 to $74_999', 'Households: $75_000 to $99_999', 
 'Households: $100_000 to $124_999', 'Households: $125_000 to $149_999', 'Households: $150_000 to $199_999',
 'Households: $200_000 or More', 'Per capita income (In 2014 Inflation adjusted dollars)', 'Gini Index']]

In [36]:
all_nyc.to_csv('all_nyc_sa_all_features.csv',index=False)
all_nyc_map.to_csv('all_nyc_sa_for_map.csv',index=False)

In [30]:
# And plotting it with a basemap
f, ax = plt.subplots(1, figsize=(10,10))
all_nyc.plot(column='quadrant', scheme='QUANTILES', k=4, alpha=1.0, colormap='Reds');
mplleaflet.display(crs=all_nyc.crs)